## Setup

In [1]:
import os
from argparse import Namespace
from collections import Counter
import json
import re
import string
import collections

from argparse import Namespace

import numpy as np
import pandas as pd
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import Dataset, DataLoader
from tqdm.notebook import tqdm

In [2]:
import pickle
with open("processed.pkl", "rb") as f:
    df = pickle.load(f)

In [3]:
df

category  \
0      Retail & Consumer Products   
1            Government & Defence   
2               Trades & Services   
3               Trades & Services   
4               Trades & Services   
...                           ...   
29995       Hospitality & Tourism   
29996    CEO & General Management   
29997                  Accounting   
29998        Government & Defence   
29999        Government & Defence   

                                         job_description       job_type  \
0      [have, you, had, years, experience, in, fresh,...      Full Time   
1      [the, opportunity, the, client, solution, anal...      Full Time   
2      [an, innovative, business, development, role, ...      Full Time   
3      [about, the, role, we, are, seeking, an, autom...      Full Time   
4      [early, starts, and, weekend, shifts, no, expe...      Full Time   
...                                                  ...            ...   
29995  [hotel, snapshot, the, radisson, blu, plaza, s...      Full Time   
29996  [the, organisation, airservices, is, governmen...      Full Time   
29997  [about, the, company, and, role, our, client, ...      Full Time   
29998  [long, term, contract, for, months, with, poss...  Contract/Temp   
29999  [customer, service, representative, west, wyal...      Part Time   

                                       short_description job_type_target  
0      [fresh, food, produce, sebastian, waddell, goo...       full-time  
1      [desk, desirable, solution, analyst, resolutio...       full-time  
2      [laundry, sky, orange, van, focus, adelaide, w...       full-time  
3      [cvs, unsolicited, tmre, mechanical, line, spr...       full-time  
4      [teach, early, starts, store, run, weekend, gr...       full-time  
...                                                  ...             ...  
29995  [hotel, bar, offer, period, supervisory, globa...       full-time  
29996  [airservices, aviation, air, board, high, secr...       full-time  
29997  [prepare, audit, process, asx, clinic, lowered...       full-time  
29998  [grant, account, el, tempo, agenciesa, client,...           other  
29999  [nsw, service, customer, opening, application,...           other  

[29655 rows x 5 columns]

## Vocabulary

In [3]:
class Vocabulary(object):
    """Class to process text and extract Vocabulary for mapping"""
    def __init__(self, token_to_idx=None, add_unk=True, unk_token="<UNK>"):
        """
        Args:
            token_to_idx (dict): a pre-existingmap of tokens to indices
            add_unk (bool): a flag that indicates whether to add the UNK token
            unk_token (str): the UNK token to add into the Vocabulary
        """
        if token_to_idx is None:
            token_to_idx = {}
        self._token_to_idx = token_to_idx
        self._idx_to_token = {idx: token 
                                for token, idx in self._token_to_idx.items()}
        self._add_unk = add_unk
        self._unk_token = unk_token
        self.unk_index = 1
        if add_unk:
            self.unk_index = self.add_token(unk_token)
    def to_serializable(self):
        """ returns a dictionary that can be serialized """
        return {'token_to_idx': self._token_to_idx,
                'add_unk': self._add_unk,
                'unk_token': self._unk_token}
    @classmethod
    def from_serializable(cls, contents):
        """ instantiates the Vocabulary from a serialized dictionary """
        return cls(**contents)
    def add_token(self, token):
        """Update mapping dicts based on the token.
        Args:
            token (str): the item to add into the Vocabulary
        Returns:
            index (int): the integer corresponding to the token
        """
        if token in self._token_to_idx:
            index = self._token_to_idx[token]
        else:
            index = len(self._token_to_idx)
            self._token_to_idx[token] = index
            self._idx_to_token[index] = token
        return index
    
    def add_many(self, tokens):
        """Add a list of tokens into the Vocabulary
        
        Args:
            tokens (list): a list of string tokens
        Returns:
            indices (list): a list of indices corresponding to the tokens
        """
        return [self.add_token(token) for token in tokens]
    
    def lookup_token(self, token):
        """Retrieve the index associated with the token
        or the UNK index if token isn't present.
        Args:
            token (str): the token to look up
        Returns:
            index (int): the index corresponding to the token
        Notes:
            `unk_index` needs to be >=0 (having been added into the Vocabulary)
            for the UNK functionality
        """
        if self._add_unk:
            return self._token_to_idx.get(token, self.unk_index)
        else:
            return self._token_to_idx[token]
    def lookup_index(self, index):
        """Return the token associated with the index
        Args:
            index (int): the index to look up
        Returns:
            token (str): the token corresponding to the index
        Raises:
        KeyError: if the index is not in the Vocabulary
        """
        if index not in self._idx_to_token:
            raise KeyError("the index (%d) is not in the Vocabulary" % index)
        return self._idx_to_token[index]
    def __str__(self):
        return "<Vocabulary(size=%d)>" % len(self)
    def __len__(self):
        return len(self._token_to_idx)

## Sequence Vocabulary

In [4]:
# used for glove encoder
class SequenceVocabulary(Vocabulary):
    def __init__(self, token_to_idx=None, unk_token="<UNK>",
                 mask_token="<MASK>", begin_seq_token="<BEGIN>",
                 end_seq_token="<END>"):

        super(SequenceVocabulary, self).__init__(token_to_idx)

        self._mask_token = mask_token
        self._unk_token = unk_token
        self._begin_seq_token = begin_seq_token
        self._end_seq_token = end_seq_token

        self.mask_index = self.add_token(self._mask_token)
        self.unk_index = self.add_token(self._unk_token)
        self.begin_seq_index = self.add_token(self._begin_seq_token)
        self.end_seq_index = self.add_token(self._end_seq_token)

    def to_serializable(self):
        contents = super(SequenceVocabulary, self).to_serializable()
        contents.update({'unk_token': self._unk_token,
                         'mask_token': self._mask_token,
                         'begin_seq_token': self._begin_seq_token,
                         'end_seq_token': self._end_seq_token})
        return contents

    def lookup_token(self, token):
        """Retrieve the index associated with the token 
          or the UNK index if token isn't present.
        
        Args:
            token (str): the token to look up 
        Returns:
            index (int): the index corresponding to the token
        Notes:
            `unk_index` needs to be >=0 (having been added into the Vocabulary) 
              for the UNK functionality 
        """
        if self.unk_index >= 0:
            return self._token_to_idx.get(token, self.unk_index)
        else:
            return self._token_to_idx[token]

## One-hot-encoding Vectorizer

In [5]:
from collections import Counter
import string
class One_hot_Vectorizer(object):
    """ The Vectorizer which coordinates the Vocabularies and puts them to use"""
    def __init__(self, description_vocab, target_vocab):
        """
        Args:
            description_vocab (Vocabulary): maps words to integers
            target_vocab (Vocabulary): maps class labels to integers
        """
        self.description_vocab = description_vocab
        self.target_vocab = target_vocab
    def vectorize(self, description_tokenized):
        """Create a collapsed one hot vector for the job description
        Args:
            description_tokenized (list): the tokenized job description
        Returns:
            one_hot (np.ndarray): the collapsed onehot encoding
        """
        one_hot = np.zeros(len(self.description_vocab), dtype=np.float32)
        for token in description_tokenized:
            if token not in string.punctuation:
                one_hot[self.description_vocab.lookup_token(token)] = 1
        return one_hot
    @classmethod
    def from_dataframe(cls, description_df, target_cat = True, cutoff=25):
        """Instantiate the vectorizer from the dataset dataframe
        Args:
            description_df (pandas.DataFrame): the description dataset
            cutoff (int): the parameter for frequency based filtering
        Returns:
            an instance of the descriptionVectorizer
        """
        description_vocab = Vocabulary(add_unk=True)
        target_vocab = Vocabulary(add_unk=False)
        # adding category or Job_type
        if target_cat:
            for category in sorted(set(description_df.category)):
                target_vocab.add_token(category)
        
        else:
            
            for job_type in  sorted(set(description_df.job_type_target)):
                target_vocab.add_token(job_type)
        # Add top words if count > provided count
        word_counts = Counter()
        for description in description_df.job_description:
            for word in description:
                if word not in string.punctuation:
                    word_counts[word] += 1
        for word, count in word_counts.items():
            if count > cutoff:
                description_vocab.add_token(word)
        return cls(description_vocab, target_vocab)
    @classmethod
    def from_serializable(cls, contents):
        """Intantiate a descriptionVectorizer from a serializable dictionary
        Args:
            contents (dict): the serializable dictionary
        Returns:
            an instance of the descriptionVectorizer class
        """
        description_vocab = Vocabulary.from_serializable(contents['description_vocab'])
        target_vocab = Vocabulary.from_serializable(contents['target_vocab'])
        return cls(description_vocab=description_vocab, target_vocab=target_vocab)
    def to_serializable(self):
        """Create the serializable dictionary for caching
        Returns:
            contents (dict): the serializable dictionary
        """
        return {'description_vocab': self.description_vocab.to_serializable(),
                'target_vocab': self.target_vocab.to_serializable()}

In [6]:
one_hot_encoder_job_type = One_hot_Vectorizer.from_dataframe(df, target_cat = False)


#### Export one-hot encoder

In [7]:
with open("one_hot_encoder_job_type.pkl", "wb") as fp:
            pickle.dump(one_hot_encoder_job_type, fp)
        


## Data Set

In [8]:
#### Needs to be put in a different place
args = Namespace(
    train_proportion=0.7,
    val_proportion=0.10,
    test_proportion=0.20,
    output_munged_csv="description_with_splits.csv",
    seed=1337,
    
    
    # Runtime option
    cuda=True, 
    catch_keyboard_interrupt=True, 
    reload_from_files=False,
    expand_filepaths_to_save_dir=True
)

In [9]:
def set_seed_everywhere(seed, cuda):
    np.random.seed(seed)
    torch.manual_seed(seed)
    if cuda:
        torch.cuda.manual_seed_all(seed)
        
# Check CUDA
if not torch.cuda.is_available():
    args.cuda = False
    
args.device = torch.device("cuda" if args.cuda else "cpu")
print("Using CUDA: {}".format(args.cuda))

# Set seed for reproducibility
set_seed_everywhere(args.seed, args.cuda)



Using CUDA: True


In [10]:
import collections
# Splitting train by category 
# Create dict
by_category = collections.defaultdict(list)
for _, row in df.iterrows():
    by_category[row.category].append(row.to_dict())

In [11]:
# Create split data
final_list = []
np.random.seed(args.seed)
for _, item_list in sorted(by_category.items()):
    np.random.shuffle(item_list)
    n = len(item_list)
    n_train = int(args.train_proportion*n)
    n_val = int(args.val_proportion*n)
    n_test = int(args.test_proportion*n)
    
    # Give data point a split attribute
    for item in item_list[:n_train]:
        item['split'] = 'train'
    for item in item_list[n_train:n_train+n_val]:
        item['split'] = 'val'
    for item in item_list[n_train+n_val:]:
        item['split'] = 'test'  
    
    # Add to final list
    final_list.extend(item_list)

In [12]:
# Write split data to file
final_description = pd.DataFrame(final_list)

In [13]:
# Write pkl
import pickle
with open("final_description.pkl", "wb") as outp:
    pickle.dump(final_description, outp)


In [14]:
flat_list = set([item for sublist in final_description.job_description for item in sublist])

In [15]:
flat_list =flat_list.union({item for item in final_description.job_type_target.unique()})

In [16]:
flat_list = flat_list.union({item for item in final_description.category.unique()})

### Create dataset classes

#### Dataset class for feed forward neural network

In [17]:
from torch.utils.data import Dataset

class Dataset_ff(Dataset):
    def __init__(self, df, vectorizer, short_description = True):
        """
        Args:
        df (pandas.DataFrame): the dataset
        vectorizer (Vectorizer): vectorizer instantiated from dataset
        """
        self.short_description = short_description
        self.df = df
        self._vectorizer = vectorizer
        self.train_df = self.df[self.df.split=='train']
        self.train_size = len(self.train_df)
        self.val_df = self.df[self.df.split=='val']
        self.validation_size = len(self.val_df)
        self.test_df = self.df[self.df.split=='test']
        self.test_size = len(self.test_df)
        self._lookup_dict = {'train': (self.train_df, self.train_size),
                            'val': (self.val_df, self.validation_size),
                            'test': (self.test_df, self.test_size)}
        self.set_split('train')
    @classmethod
    def load_dataset_and_make_vectorizer(cls, csv):
        """Load dataset and make a new vectorizer from scratch
        Args:
            csv (str): location of the dataset
        Returns:
            an instance of Dataset
        """
        df = pd.read_csv(csv)
        return cls(df, Vectorizer.from_dataframe(df))
   
    def get_vectorizer(self):
        """ returns the vectorizer """
        return self._vectorizer
    def set_split(self, split="train"):
        """ selects the splits in the dataset using a column in the dataframe
        Args:
        split (str): one of "train", "val", or "test"
        """
        self._target_split = split
        self._target_df, self._target_size = self._lookup_dict[split]
    def __len__(self):
        return self._target_size
    def __getitem__(self, index):
        """the primary entry point method for PyTorch datasets
        Args:
        index (int): the index to the data point
        Returns:
        a dict of the data point's features (x_data) and label (y_target)
        """
        row = self._target_df.iloc[index]
        if self.short_description:
            description_vector = \
            self._vectorizer.vectorize(row.short_description)
        else:
            description_vector = \
            self._vectorizer.vectorize(row.job_description)
        target_index = \
        self._vectorizer.target_vocab.lookup_token(row.job_type_target)
        return {'x_data': description_vector,
                'y_target': target_index}
    def get_num_batches(self, batch_size):
        """Given a batch size, return the number of batches in the dataset
        Args:
        batch_size (int)
        Returns:
        number of batches in the dataset
        """
        return len(self) // batch_size

#### Create datasets

In [342]:
with open("one_hot_encoder_job_type.pkl", "rb") as fp:
           one_hot_encoder_job_type=  pickle.load( fp)
        
with open("final_description.pkl", "rb") as outp:
    final_description = pickle.load(outp)

In [343]:
dataset_one_hot_tfidf_job_type = Dataset_ff(final_description, one_hot_encoder_job_type)




In [344]:
import pickle
with open("dataset_one_hot_tfidf_job_type.pkl", "wb") as outp:
    pickle.dump(dataset_one_hot_tfidf_job_type, outp)
   

    


## Classifiers

###  Feed forward Neural network

#### Perceptron Classifier

Initialising a one hidden layer Perceptron to be used for the feed forward Neural network.

In [24]:
import torch.nn as nn
import torch.nn.functional as F
class Classifier(nn.Module):
    """ a simple perceptron-based classifier """
    def __init__(self, num_features):
        """
        Args:
            num_features (int): the size of the input feature vector
        """
        super(Classifier, self).__init__()
        self.fc1 = nn.Linear(in_features=num_features, out_features=1)
    
    def forward(self, x_in, apply_sigmoid=False):
        """The forward pass of the classifier
        Args:
            x_in (torch.Tensor): an input data tensor 
                    x_in.shape should be (batch, num_features)
            apply_sigmoid (bool): a flag for the sigmoid activation
                    should be false if used with the cross-entropy losses
        Returns:
            the resulting tensor. tensor.shape should be (batch,).
        """
        y_out = self.fc1(x_in).squeeze()
        
        if apply_sigmoid:
            y_out = torch.sigmoid(y_out)
        return y_out

### Training

### Setup

In [19]:
from argparse import Namespace
args_oh_ff = Namespace(
    # Data and path information
    model_state_file='model.pth',
    save_dir='./model_storage/document_classification/',
    # No model hyperparameters
    # Training hyperparameters
    batch_size=128,
    early_stopping_criteria=5,
    learning_rate=0.001,
    num_epochs=100,
    seed=1337,
    # Runtime options
    cuda=True,
    device='cuda',
)

In [20]:
import torch
import torch.optim as optim
import pandas as pd

def make_train_state(args_oh_ff):
    return {'epoch_index': 0,
            'train_loss': [],
            'train_acc': [],
            'val_loss': [],
            'val_acc': [],
            'test_loss': 1,
            'test_acc': 1}

if not torch.cuda.is_available():
    args_oh_ff.cuda = False
args_oh_ff.device = torch.device("cuda" if args_oh_ff.cuda else "cpu")

In [21]:
def compute_accuracy(y_pred, y_target):
    y_target = y_target.cpu()
    y_pred_indices = (torch.sigmoid(y_pred)>0.5).cpu().long()#.max(dim=1)[1]
    n_correct = torch.eq(y_pred_indices, y_target).sum().item()
    return n_correct / len(y_pred_indices) * 100

In [45]:

def generate_batches(dataset, batch_size, shuffle=True,
                     drop_last=True, device="cpu"): 
    """
    A generator function which wraps the PyTorch DataLoader. It will 
      ensure each tensor is on the write device location.
    """
    dataloader = DataLoader(dataset=dataset, batch_size=batch_size,
                            shuffle=shuffle, drop_last=drop_last)

    for data_dict in dataloader:
        out_data_dict = {}
        for name, tensor in data_dict.items():
            out_data_dict[name] = data_dict[name].to(device)
        yield out_data_dict

### Onehot Encoding Data set TFIDF

Training and testing for the one hot encoding data set with top 10 TFIDF words.

Preparing
* Model
* Loss Function
* Optizimer

In [154]:
train_state = make_train_state(args_oh_ff)


# dataset and vectorizer
with open("dataset_one_hot_tfidf_job_type.pkl", "rb") as f:
    dataset = pickle.load(f)

vectorizer = dataset.get_vectorizer()
# model
classifier = Classifier(num_features=len(vectorizer.description_vocab))
classifier = classifier.to(args_oh_ff.device)
# loss and optimizer
loss_func = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(classifier.parameters(), lr=args_oh_ff.learning_rate)

In [155]:
import numpy as np
for epoch_index in range(args_oh_ff.num_epochs):
    train_state['epoch_index'] = epoch_index
    # Iterate over training dataset
    # setup: batch generator, set loss and acc to 0, set train mode on
    dataset.set_split('train')
    batch_generator = generate_batches(dataset, batch_size=args_oh_ff.batch_size, device=args_oh_ff.device)
    running_loss = 0.0
    running_acc = 0.0
    classifier.train()
    for batch_index, batch_dict in enumerate(batch_generator):
        # the training routine is 5 steps:
        # step 1. zero the gradients
        optimizer.zero_grad()
        # step 2. compute the output
        y_pred = classifier(x_in=batch_dict['x_data'].float())
        # step 3. compute the loss
        loss = loss_func(y_pred, batch_dict['y_target'].float())
        loss_batch = loss.item()
        running_loss += (loss_batch-running_loss) / (batch_index + 1)
        # step 4. use loss to produce gradients
        loss.backward()
        # step 5. use optimizer to take gradient step
        optimizer.step()
        # compute the accuracy
        acc_batch = compute_accuracy(y_pred, batch_dict['y_target'])
        running_acc += (acc_batch - running_acc) / (batch_index + 1)

    train_state['train_loss'].append(running_loss)
    train_state['train_acc'].append(running_acc)

    # Iterate over val dataset
    # setup: batch generator, set loss and acc to 0, set eval mode on
    dataset.set_split('val')
    batch_generator = generate_batches(dataset, batch_size=args_oh_ff.batch_size, device=args_oh_ff.device)
    running_loss = 0.
    running_acc = 0.
    classifier.eval()

    for batch_index, batch_dict in enumerate(batch_generator):
        # step 1. compute the output
        y_pred = classifier(x_in=batch_dict['x_data'].float())
        # step 2. compute the loss
        loss = loss_func(y_pred, batch_dict['y_target'].float())
        loss_batch = loss.item()
        running_loss += (loss_batch - running_loss) / (batch_index + 1)
        # step 3. compute the accuracy
        acc_batch = compute_accuracy(y_pred, batch_dict['y_target'])
        running_acc += (acc_batch - running_acc) / (batch_index + 1)
    train_state['val_loss'].append(running_loss)
    train_state['val_acc'].append(running_acc)

In [158]:
with open(f"{args_oh_ff.save_dir}/ff_neuralNetwork_oneHotEncoding_jobType.pth", "wb") as outp:
    pickle.dump(classifier, outp)


#### Model Evaluation

In [25]:
with open(f"{args_oh_ff.save_dir}/ff_neuralNetwork_oneHotEncoding_jobType.pth", "rb") as f:
    classifier = pickle.load(f)

In [29]:
with open("dataset_one_hot_tfidf_job_type.pkl", "rb") as f:
    dataset = pickle.load(f)

train_state = make_train_state(args_oh_ff)
loss_func = nn.BCEWithLogitsLoss()
dataset.set_split('test')
batch_generator = generate_batches(dataset,batch_size=args_oh_ff.batch_size,device=args_oh_ff.device)
running_loss = 0.
running_acc = 0.
classifier.eval()
for batch_index, batch_dict in enumerate(batch_generator):
    # compute the output
    y_pred = classifier(x_in=batch_dict['x_data'].float())
    # compute the loss
    loss = loss_func(y_pred, batch_dict['y_target'].float())
    loss_batch = loss.item()
    running_loss += (loss_batch - running_loss) / (batch_index + 1)
    # compute the accuracy
    acc_batch = compute_accuracy(y_pred, batch_dict['y_target'])
    running_acc += (acc_batch - running_acc) / (batch_index + 1)
train_state['test_loss'] = running_loss
train_state['test_acc'] = running_acc

In [30]:
print("Test loss: {:.3f}".format(train_state['test_loss']))
print("Test Accuracy: {:.2f}".format(train_state['test_acc']))

Test loss: 0.587
Test Accuracy: 74.90


### Glove Encoding

### Loading glove embedding

In [32]:
def load_embedding_model():
    """ Load GloVe Vectors
        Return:
            wv_from_bin: All 400000 embeddings, each lengh 200
    """
    import gensim.downloader as api
    wv_pretrained = api.load("glove-wiki-gigaword-200")
    print("Loaded vocab size %i" % len(wv_pretrained))
    print("The loaded object is of type %s" % str(type(wv_pretrained)))
    return wv_pretrained

In [33]:
# -----------------------------------
# Run Cell to Load Word Vectors
# Note: This will take several minutes 
# (8 mins in my case )
# -----------------------------------
wv_pretrained = load_embedding_model()

Loaded vocab size 400000
The loaded object is of type <class 'gensim.models.keyedvectors.KeyedVectors'>


In [20]:
def get_matrix_of_vectors(wv_pretrained, required_words):
    """ Put the GloVe vectors into a matrix M.
        Param:
            wv_pretrained: KeyedVectors object; the 400000 GloVe vectors loaded from file
        Return:
            M: numpy matrix shape (num words, 200) containing the vectors
            word2Ind: dictionary mapping each word to its row number in M
    """
    import random
    words = list(wv_pretrained.key_to_index.keys())
    print("Shuffling words ...")
    random.seed(224)
    random.shuffle(words)
    words = words[:10000]
    print("Putting %i words into word2Ind and matrix M..." % len(words))
    word2Ind = {}
    M = []
    curInd = 0
    for w in words:
        try:
            M.append(wv_pretrained.get_vector(w, norm=True))
            word2Ind[w] = curInd
            curInd += 1
        except KeyError:
            continue
    for w in required_words:
        if w in words:
            continue
        try:
            M.append(wv_pretrained.get_vector(w, norm=True))
            word2Ind[w] = curInd
            curInd += 1
        except KeyError:
            continue
    M = np.stack(M)
    print("Done.")
    return M, word2Ind

##### Adding rare words from the data set

In [35]:
# Adding rare words from the dataset
M, word2Ind = get_matrix_of_vectors(wv_pretrained, flat_list)

Shuffling words ...
Putting 10000 words into word2Ind and matrix M...
Done.


### Vecotorizer 

#### Creating a glove vectorizer class to be used in creating the data set

In [23]:
class emb_Vectorizer(object):
    """ The Vectorizer which coordinates the Vocabularies and puts them to use"""    
    def __init__(self, desc_vocab, target_vocab):
        self.description_vocab = desc_vocab
        self.target_vocab = target_vocab

    def vectorize(self, description, vector_length=-1):
        """
        Args:
            description (list) : tokenized description 
            vector_length (int): an argument for forcing the length of index vector
        Returns:
            the vetorized description (numpy.array)
        """
        indices = []
        
        
        indices.extend(self.description_vocab.lookup_token(token) 
                       for token in description)
        if vector_length < 0:
            vector_length = len(indices)
        
        out_vector = np.zeros(vector_length, dtype=np.int64)
     
        out_vector[:len(indices)] = indices
       

        return out_vector

    @classmethod
    def from_dataframe(cls, description_df, target_cat = True, cutoff=25):
        """Instantiate the vectorizer from the dataset dataframe
        
        Args:
            description_df (pandas.DataFrame): the target dataset
            cutoff (int): frequency threshold for including in Vocabulary 
        Returns:
            an instance of the descriptionVectorizer
        """
        description_vocab = Vocabulary(add_unk=True)
        target_vocab = Vocabulary(add_unk=False)
        if target_cat:
            for target in sorted(set(description_df.category)):
                target_vocab.add_token(target)
        
        else:
            for job_type in sorted(set(description_df.job_type_target)):
                target_vocab.add_token(job_type)
            
            
        word_counts = Counter()
        for description in description_df.job_description:
            for token in description:
                if token not in string.punctuation:
                    word_counts[token] += 1
        
        description_vocab = SequenceVocabulary()
        for word, word_count in word_counts.items():
            if word_count >= cutoff:
                description_vocab.add_token(word)
        
        return cls(description_vocab, target_vocab)

    @classmethod
    def from_serializable(cls, contents):
        description_vocab = \
            SequenceVocabulary.from_serializable(contents['description_vocab'])
        target_vocab =  \
            Vocabulary.from_serializable(contents['target_vocab'])

        return cls(description_vocab=description_vocab, target_vocab=target_vocab)

    def to_serializable(self):
        return {'description_vocab': self.description_vocab.to_serializable(),
                'target_vocab': self.target_vocab.to_serializable()}

In [ ]:
with open("final_description.pkl", "rb") as outp:
    final_description = pickle.load(outp)

In [141]:
glove_job_type_vec = emb_Vectorizer.from_dataframe(final_description, target_cat = False) 
glove_category_vec = emb_Vectorizer.from_dataframe(final_description, target_cat = True)
# swapping the document based word to ind for the pretained embedding based word to ind for description
glove_job_type_vec.description_vocab = Vocabulary(token_to_idx=word2Ind, add_unk=True)
glove_category_vec.description_vocab = Vocabulary(token_to_idx=word2Ind, add_unk=True)

In [142]:
with open("glove_job_type_vec.pkl", "wb") as outp:
    pickle.dump(glove_job_type_vec, outp)
   

with open("glove_category_vec.pkl", "wb") as outp:
    pickle.dump(glove_category_vec, outp)

### Data set

In [28]:
class Dataset_embedding(Dataset):
    def __init__(self, df, vectorizer, short = True, job_type = True):
        """
        Args:
            df (pandas.DataFrame): the dataset
            vectorizer (GloveVectorizer): vectorizer instatiated from dataset
        """
        self.df = df
        self._vectorizer = vectorizer
        self.short = short
        self.job_type = job_type

        # +1 if only using begin_seq, +2 if using both begin and end seq tokens
        measure_len = lambda context: len(context)
        if self.short:
            self._max_seq_length = max(map(measure_len, df.short_description))
        else:
            self._max_seq_length = max(map(measure_len, df.job_description)) 
        

        self.train_df = self.df[self.df.split=='train']
        self.train_size = len(self.train_df)

        self.val_df = self.df[self.df.split=='val']
        self.validation_size = len(self.val_df)

        self.test_df = self.df[self.df.split=='test']
        self.test_size = len(self.test_df)

        self._lookup_dict = {'train': (self.train_df, self.train_size),
                             'val': (self.val_df, self.validation_size),
                             'test': (self.test_df, self.test_size)}

        self.set_split('train')

        # Class weights
        if self.job_type:
            class_counts = df.job_type_target.value_counts().to_dict()
        else:
            class_counts = df.category.value_counts().to_dict()
        def sort_key(item):
            return self._vectorizer.target_vocab.lookup_token(item[0])
        
        sorted_counts = sorted(class_counts.items(), key=sort_key)
        frequencies = [count for _, count in sorted_counts]
        self.class_weights = 1.0 / torch.tensor(frequencies, dtype=torch.float32)
        
        
    @classmethod
    def load_dataset_and_make_vectorizer(cls, csv):
        """Load dataset and make a  vectorizer from scratch
        
        Args:
            csv (str): location of the dataset
        Returns:
            an instance of Dataset
        """
        df = pd.read_csv(csv)
        train_df = df[df.split=='train']
        return cls(df, gloveVectorizer.from_dataframe(train_df))

    @classmethod
    def load_dataset_and_load_vectorizer(cls, csv, vectorizer_filepath):
        """Load dataset and the corresponding vectorizer. 
        Used in the case in the vectorizer has been cached for re-use
        
        Args:
            csv (str): location of the dataset
            vectorizer_filepath (str): location of the saved vectorizer
        Returns:
            an instance of Dataset
        """
        df = pd.read_csv(csv)
        vectorizer = cls.load_vectorizer_only(vectorizer_filepath)
        return cls(csv, vectorizer)

    @staticmethod
    def load_vectorizer_only(vectorizer_filepath):
        """a static method for loading the vectorizer from file
        
        Args:
            vectorizer_filepath (str): the location of the serialized vectorizer
        Returns:
            an instance of GloveVectorizer
        """
        with open(vectorizer_filepath) as fp:
            return GloveVectorizer.from_serializable(json.load(fp))

    def save_vectorizer(self, vectorizer_filepath):
        """saves the vectorizer to disk using json
        
        Args:
            vectorizer_filepath (str): the location to save the vectorizer
        """
        with open(vectorizer_filepath, "w") as fp:
            json.dump(self._vectorizer.to_serializable(), fp)

    def get_vectorizer(self):
        """ returns the vectorizer """
        return self._vectorizer

    def set_split(self, split="train"):
        """ selects the splits in the dataset using a column in the dataframe """
        self._target_split = split
        self._target_df, self._target_size = self._lookup_dict[split]

    def __len__(self):
        return self._target_size

    def __getitem__(self, index):
        """the primary entry point method for PyTorch datasets
        
        Args:
            index (int): the index to the data point 
        Returns:
            a dictionary holding the data point's features (x_data) and label (y_target)
        """
        row = self._target_df.iloc[index]

        if self.short:
            description_vector = \
                self._vectorizer.vectorize(row.short_description, self._max_seq_length)
        else:
            description_vector = \
                self._vectorizer.vectorize(row.job_description, self._max_seq_length)

        if self.job_type:
            target_index = \
                self._vectorizer.target_vocab.lookup_token(row.job_type_target)
        else:
            target_index = \
                self._vectorizer.target_vocab.lookup_token(row.category)


        return {'x_data': description_vector,
                'y_target': target_index}

    def get_num_batches(self, batch_size):
        """Given a batch size, return the number of batches in the dataset
        
        Args:
            batch_size (int)
        Returns:
            number of batches in the dataset
        """ 
        return len(self) // batch_size


#### Create dataset

In [144]:
with open("glove_job_type_vec.pkl", "rb") as f:
    glove_job_type_vec = pickle.load(f)
    

with open("glove_category_vec.pkl", "rb") as f:
    glove_category_vec = pickle.load(f)
    
with open("final_description.pkl", "rb") as outp:
    final_description = pickle.load(outp)

In [145]:
dataset_glove_tfidf_job_type = Dataset_embedding(final_description, glove_job_type_vec)
dataset_glove_full_desc_job_type = Dataset_embedding(final_description,glove_job_type_vec, short = False)
dataset_glove_full_desc_category = Dataset_embedding(final_description,glove_category_vec, short = False, job_type = False)


In [146]:
with open("dataset_glove_tfidf_job_type.pkl", "wb") as outp:
    pickle.dump(dataset_glove_tfidf_job_type, outp)
   
    
with open("dataset_glove_full_desc_job_type.pkl", "wb") as outp:
    pickle.dump(dataset_glove_full_desc_job_type, outp)
    
# with open("dataset_glove_full_desc_category.pkl", "wb") as outp:
#     pickle.dump(dataset_glove_full_desc_category, outp)

In [147]:
# with open("dataset_glove_tfidf_job_type.pkl", "rb") as f:
#     temp = pickle.load(f)

# extracting input size

dataloader = DataLoader(dataset=dataset_glove_tfidf_job_type, batch_size=1,
                            shuffle=True, drop_last=True)
for data_dict in dataloader:
    for name, tensor in data_dict.items():
        print(name)
        print(data_dict[name])
        print(data_dict[name].size())
    

x_data
tensor([[18871, 16321, 41165, 43136, 35641, 38542, 30475, 10702, 28725, 42456]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[34637, 18338, 43136, 28676, 19066, 41827, 17017, 34655, 13003, 18388]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[28663, 30313, 35393, 34618, 24981, 12988, 21971, 19848, 42570, 19168]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[30455, 16336, 13290, 11897, 41940, 25652, 21717, 30598, 22998, 20017]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[40340, 43136, 14494, 29328, 12372, 39762, 13197, 38723, 14781, 25327]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[21939, 14781, 15213, 10715, 22603, 43136, 27559, 36281, 36265, 13423]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[43136, 25652, 30475, 14244, 19311, 41353, 17114, 14003, 19576, 34767]])
torch.Size([1, 10])
y_target
tensor([1])
t

x_data
tensor([[22212, 29328, 39757, 35393, 10178,  8760, 35426, 25485, 20197, 29189]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[43136, 12338, 41307, 29818, 36157, 40261, 10114, 17709, 36477, 34134]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[34550, 15159, 17781, 30385, 28163, 10000, 38338, 43136, 23489,  4537]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[39762, 25652, 35179, 37861, 23193, 36147, 34547, 36863, 15631, 39464]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[43136, 40587, 28266, 32464, 25877, 31162, 34939, 19424, 31774, 24244]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[12861, 34166, 20840, 13864, 33768, 19139, 43136, 28557, 18355, 32083]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[10744, 10976,   921, 22105, 22561, 43136, 18675, 33327, 20136,   433]])
torch.Size([1, 10])
y_target
tensor([0])
t

x_data
tensor([[14258, 11510, 43136, 43136, 39145, 11520, 13264, 21424, 36190, 10023]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[40736, 27238, 41253, 29584, 23296, 17717, 37957, 40851, 14669, 17500]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[19389, 21000, 38526, 34833, 35016, 17707, 41112, 33118, 35125, 41013]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[18108, 41572, 29395, 37593, 16710, 17390, 23057, 28018, 14669, 40010]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[29689, 10996, 19308, 11024, 14615, 34311, 25856, 19347, 38709, 38761]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[39762, 37623, 29395, 18345, 36243, 25953, 31163, 19282, 22257,  4546]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[43136, 25786, 27032, 26999, 17445, 43136, 35595, 29692, 43136, 32881]])
torch.Size([1, 10])
y_target
tensor([0])
t

tensor([[23416,  4537, 36160, 24585, 43136, 29915, 25778, 12961, 33026, 35101]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[43136, 34304, 38585, 36772, 24166, 19135, 42691, 40446, 33415, 18616]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[23975, 16057, 40429, 19135, 32228, 16911, 43136, 21381, 10382, 43136]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[34793, 38601, 28341, 41811, 26752, 18887, 40505, 25370, 26199, 24669]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[15380, 14851, 14217, 28214, 35778, 12864, 36243, 35545, 34618, 23374]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[10684, 14684, 36569, 38811, 34568, 23464, 11902, 34023, 14779, 20794]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[39408, 42938, 27699, 28908, 31437, 18488, 15389, 30897, 21565, 16539]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Si

tensor([[30898, 25351, 35622, 10339, 27215, 18488, 42193, 26779, 27079, 13017]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[25469, 43136, 29233,   796, 27962,  6698, 19073, 39369, 21719, 25157]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[43136, 23809, 13815, 16047, 37711, 43136, 23699, 40682, 18788,  3178]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[35133, 23843, 27780, 35289, 13879, 31610, 11288, 11739, 11268, 43136]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[33671, 11796, 10701, 26292, 43136, 41683, 16357, 19945, 26106, 30151]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[25652, 27032, 10338, 37870, 34767, 41341, 15328, 29467, 11220, 33301]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[37671, 26447, 26873, 43136, 43136, 15695, 25226, 31327, 37799, 42475]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Si

...

x_data
tensor([[18965, 20148, 43136, 18980, 43136, 31373, 43136, 39891, 23790, 27566]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[25652, 31539, 29305, 25953, 19178, 39097, 40391, 34397, 19738, 33327]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[24163, 13936, 10467, 31682, 23487, 21447, 24249, 17968, 30724, 23551]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[43136, 34550, 43136, 42250, 22603, 28718,  1948, 23405, 31320, 20482]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[28048, 15811, 17141, 41699, 12317, 16307, 35395, 10616, 10942, 31774]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[18288, 11347, 25296, 10996, 22100, 34589, 41724, 23471, 28171, 16108]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[40724, 43136, 27174, 27960, 13864, 12861, 38943, 41651, 19139, 14781]])
torch.Size([1, 10])
y_target
tensor([0])
t

tensor([[16467, 12641, 13963, 31827, 21659, 42969, 18388, 10883, 41199, 40748]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[19135, 17728, 17990, 37145, 18598, 18896, 15252, 36231, 30231, 11286]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[31143, 10178, 29547, 30432, 12463, 22191, 36810, 25370, 43136, 38709]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[28008, 39623, 11613, 22651, 29039, 31482, 28221, 23416, 31803, 10285]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[26289, 29858, 32952, 25750, 21418, 33790, 10775, 31645, 16355, 23163]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[39114, 43136, 12343, 35953, 16138, 40964, 17748, 24899, 32452, 39919]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[23015, 20849, 35289, 27126, 19657, 43136, 25337, 16138, 37593, 13492]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Si

tensor([0])
torch.Size([1])
x_data
tensor([[32514, 20630, 17250, 35215, 30623, 19041, 36811, 21634, 23489, 19430]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[43136, 14145, 42308, 27832, 43136, 33232, 20980, 24286, 16633, 39790]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[11948, 41731, 28194, 43136, 17316, 17668, 43136, 31224, 10516, 13459]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[43136, 15447, 10798, 30184, 11837, 19378, 36641, 33636, 29256, 36345]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[17390, 17717, 43136, 36154, 13971, 23337, 10531,  8418, 27342, 12334]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[30864, 19661, 39874, 38326, 15436, 19386, 38947, 11154, 28371, 24026]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[25652, 32989, 34833, 37730, 43035, 32422, 26339, 14781, 23843, 22565]])
torch.Size([1,

x_data
tensor([[27559, 43136, 34833, 41981, 21089, 23215, 19686, 33882, 33122, 42154]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[27410, 27956, 43136, 32011, 31774, 32834, 18475, 18821, 11236, 27289]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[42742, 26288, 35122, 18890, 34833, 42699, 18960, 28959, 17417, 12239]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[43136, 17124, 14977, 42938, 16691, 36950, 14047, 14137, 36345, 17017]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[30185, 26069, 16614, 23259, 18948, 11286, 30299, 30552, 38006, 25534]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[17030, 43035, 27687, 34227, 43136, 20080, 24856, 35512, 41467, 27078]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[21703, 14435, 25652, 26789, 35368, 43136, 42905, 17505, 40577, 30885]])
torch.Size([1, 10])
y_target
tensor([0])
t

x_data
tensor([[21851, 25370, 28521, 29331, 31320, 16710, 20595, 41517, 36634, 38007]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[21783, 10023, 33768, 29316, 26959, 11135, 27981, 34715, 11994, 27102]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[26812, 18862, 43136, 43136, 30758, 20462, 25922, 42971, 31104, 35581]])
torch.Size([1, 10])
y_target
tensor([0])
torch.Size([1])
x_data
tensor([[36582, 27004, 43136, 31320, 43136, 43136, 19710, 43136, 15344, 12631]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[34421, 27409, 31418, 12858, 17640, 24249, 15436, 25879, 42609, 16964]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[43136, 40587, 32464, 31882, 32444, 15927, 28266, 31162, 34939, 31774]])
torch.Size([1, 10])
y_target
tensor([1])
torch.Size([1])
x_data
tensor([[39036, 43136, 23006, 27632, 19910, 43136, 43136, 43136, 23446, 15357]])
torch.Size([1, 10])
y_target
tensor([0])
t

## Training

In [56]:
class Classifier_emb(nn.Module):
    def __init__(self, embedding_size, num_embeddings, 
                 hidden_dim,  input_size, dropout_p,
                 pretrained_embeddings=None):
        """
        Args:
            embedding_size (int): size of the embedding vectors
            num_embeddings (int): number of embedding vectors
            filter_width (int): width of the convolutional kernels
            num_channels (int): number of convolutional kernels per layer
            hidden_dim (int): the size of the hidden dimension
            num_classes (int): the number of classes in classification
            dropout_p (float): a dropout parameter 
            pretrained_embeddings (numpy.array): previously trained word embeddings
                default is None. If provided, 
            padding_idx (int): an index representing a null position
        """
        super(Classifier_emb, self).__init__()

        if pretrained_embeddings is None:

            self.emb = nn.Embedding(embedding_dim=embedding_size,
                                    num_embeddings=num_embeddings
                                    )        
        else:
            pretrained_embeddings = torch.from_numpy(pretrained_embeddings).float()
            self.emb = nn.Embedding(embedding_dim=embedding_size,
                                    num_embeddings=num_embeddings,
                                    _weight=pretrained_embeddings)
        
        self._dropout_p = dropout_p    
       
        self.fc1 = nn.Linear(
           input_size * embedding_size, 
            out_features=1
        )
        
       

    def forward(self, x_in, apply_sigmoid=False):
        """The forward pass of the classifier
        
        Args:
            x_in (torch.Tensor): an input data tensor. 
                x_in.shape should be (batch, dataset._max_seq_length)
            apply_softmax (bool): a flag for the softmax activation
                should be false if used with the Cross Entropy losses
        Returns:
            the resulting tensor. tensor.shape should be (batch, num_classes)
        """
        # mlp classifier
       
        
        x_embedded = self.emb(x_in).view(x_in.size()[0], -1)
        
        prediction_vector = self.fc1(x_embedded).squeeze()
        if apply_sigmoid:
            prediction_vector = torch.sigmoid(prediction_vector)

        return prediction_vector

In [149]:
args_glove = Namespace(
    # Data and Path hyper parameters
    
    # Model hyper parameters 
    use_glove=False, 
    hidden_dim=100, 
    input_size = 10, # Since we are using top ten tfidf
    vocab_siz = len(flat_list),
    embedding_dim = 200,
    target_dim = 2, # only need Full time and other.
    # Training hyper parameter
    seed=1337, 
    learning_rate=0.001, 
    batch_size=128,
    dropout_p=0.1, 
    num_epochs=100, 
    early_stopping_criteria=5, 
    # Runtime option
    cuda=True, 
    catch_keyboard_interrupt=True, 
    reload_from_files=False,
    expand_filepaths_to_save_dir=True,
    model_state_file="glove_tfidf_model.pth",
    save_dir='./model_storage/document_classification/',
) 


    
# Check CUDA
if not torch.cuda.is_available():
    args_glove.cuda = False
    
args_glove.device = torch.device("cuda" if args_glove.cuda else "cpu")
print("Using CUDA: {}".format(args_glove.cuda))

# Set seed for reproducibility
set_seed_everywhere(args_glove.seed, args_glove.cuda)



Using CUDA: True


### Helper Functions

In [38]:
def make_embedding_matrix(words, embeddings , word_to_idx, emb_dim, seed, filepath= None):
    """
    Create embedding matrix for a specific set of words.
    
    Args:
        filepath (str): file path to the embeddigns
        words (list): list of words in the dataset
    """
    import numpy
    numpy.random.seed(seed)
    
    if filepath != None:
        word_to_idx, embeddings = load_from_file(filepath)
    embedding_size = embeddings.shape[1]
    
    final_embeddings = np.zeros((len(words), embedding_size))

    for i, word in enumerate(words):
        if word == '<UNK>':
            final_embeddings[i, :] = np.random.uniform(-1,1, emb_dim)
        elif word in word_to_idx:
            final_embeddings[i, :] = embeddings[word_to_idx[word]]
        else:
            embedding_i = torch.ones(1, embedding_size)
            torch.nn.init.xavier_uniform_(embedding_i)
            final_embeddings[i, :] = embedding_i

    return final_embeddings

def make_train_state(args):
    return {'stop_early': False,
            'early_stopping_step': 0,
            'early_stopping_best_val': 1e8,
            'learning_rate': args.learning_rate,
            'epoch_index': 0,
            'train_loss': [],
            'train_acc': [],
            'val_loss': [],
            'val_acc': [],
            'test_loss': -1,
            'test_acc': -1,
            'model_filename': args.model_state_file
            
          }

def update_train_state(args, model, train_state):
    """Handle the training state updates.

    Components:
     - Early Stopping: Prevent overfitting.
     - Model Checkpoint: Model is saved if the model is better

    :param args: main arguments
    :param model: model to train
    :param train_state: a dictionary representing the training state values
    :returns:
        a new train_state
    """

    # Save one model at least
    if train_state['epoch_index'] == 0:
        torch.save(model.state_dict(), train_state['model_filename'])
        train_state['stop_early'] = False

    # Save model if performance improved
    elif train_state['epoch_index'] >= 1:
        loss_tm1, loss_t = train_state['val_loss'][-2:]

        # If loss worsened
        if loss_t >= train_state['early_stopping_best_val']:
            # Update step
            train_state['early_stopping_step'] += 1
        # Loss decreased
        else:
            # Save the best model
            if loss_t < train_state['early_stopping_best_val']:
                torch.save(model.state_dict(), train_state['model_filename'])

            # Reset early stopping step
            train_state['early_stopping_step'] = 0

        # Stop early ?
        train_state['stop_early'] = \
            train_state['early_stopping_step'] >= args.early_stopping_criteria

    return train_state

def compute_accuracy(y_pred, y_target):
    y_target = y_target.cpu()
    y_pred_indices = (torch.sigmoid(y_pred)>0.5).cpu().long()#.max(dim=1)[1]
    n_correct = torch.eq(y_pred_indices, y_target).sum().item()
    return n_correct / len(y_pred_indices) * 100



### Initialising

In [151]:
args_glove.use_glove = True
measure_len = lambda context: len(context) 
args_glove.input_size = max(map(measure_len, df.short_description))

# dataset and vectorizer
with open("dataset_glove_tfidf_job_type.pkl", "rb") as f:
    dataset = pickle.load(f)

vectorizer = dataset.get_vectorizer()

# Use GloVe or randomly initialized embeddings
if args_glove.use_glove:
    words = vectorizer.description_vocab._token_to_idx.keys()
    glove_embedding = make_embedding_matrix(words,embeddings=M, seed = args_glove.seed, emb_dim=args_glove.embedding_dim,word_to_idx=word2Ind )
    print("Using pre-trained embeddings")

# model
classifier_emb_tfidf = Classifier_emb(embedding_size=args_glove.embedding_dim, 
                            num_embeddings=len(vectorizer.description_vocab),
                            hidden_dim=args_glove.hidden_dim, 
                            input_size = args_glove.input_size,
                            dropout_p=args_glove.dropout_p,
                            pretrained_embeddings=glove_embedding)



Using pre-trained embeddings


In [152]:
classifier_emb_tfidf = classifier_emb_tfidf.to(args_glove.device)
dataset.class_weights = dataset.class_weights.to(args_glove.device)
    
loss_func = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(classifier_emb_tfidf.parameters(), lr=args_glove.learning_rate)
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer=optimizer,
                                           mode='min', factor=0.5,
                                           patience=1)

train_state_glove = make_train_state(args_glove)

epoch_bar = tqdm(desc='training routine', 
                          total=args_glove.num_epochs,
                          position=0)

dataset.set_split('train')
train_bar = tqdm(desc='split=train',
                          total=dataset.get_num_batches(args_glove.batch_size), 
                          position=1, 
                          leave=True)
dataset.set_split('val')
val_bar = tqdm(desc='split=val',
                        total=dataset.get_num_batches(args_glove.batch_size), 
                        position=1, 
                        leave=True)

try:
    for epoch_index in range(args_glove.num_epochs):
        train_state_glove['epoch_index'] = epoch_index

        # Iterate over training dataset

        # setup: batch generator, set loss and acc to 0, set train mode on

        dataset.set_split('train')
        batch_generator = generate_batches(dataset, 
                                           batch_size=args_glove.batch_size, 
                                           device=args_glove.device)
        running_loss = 0.0
        running_acc = 0.0
        classifier_emb_tfidf.train()

        for batch_index, batch_dict in enumerate(batch_generator):
            # the training routine is these 5 steps:

            # --------------------------------------
            # step 1. zero the gradients
            optimizer.zero_grad()

            # step 2. compute the output
            y_pred = classifier_emb_tfidf(batch_dict['x_data'])

            # step 3. compute the loss
            loss = loss_func(y_pred, batch_dict['y_target'].float())
            loss_t = loss.item()
            running_loss += (loss_t - running_loss) / (batch_index + 1)

            # step 4. use loss to produce gradients
            loss.backward()

            # step 5. use optimizer to take gradient step
            optimizer.step()
            # -----------------------------------------
            # compute the accuracy
            acc_t = compute_accuracy(y_pred, batch_dict['y_target'])
            running_acc += (acc_t - running_acc) / (batch_index + 1)

            # update bar
            train_bar.set_postfix(loss=running_loss, acc=running_acc, 
                                  epoch=epoch_index)
            train_bar.update()

        train_state_glove['train_loss'].append(running_loss)
        train_state_glove['train_acc'].append(running_acc)

        # Iterate over val dataset

        # setup: batch generator, set loss and acc to 0; set eval mode on
        dataset.set_split('val')
        batch_generator = generate_batches(dataset, 
                                           batch_size=args_glove.batch_size, 
                                           device=args_glove.device)
        running_loss = 0.
        running_acc = 0.
        classifier_emb_tfidf.eval()

        for batch_index, batch_dict in enumerate(batch_generator):

            # compute the output
            y_pred =  classifier_emb_tfidf(batch_dict['x_data'])

            # step 3. compute the loss
            loss = loss_func(y_pred, batch_dict['y_target'].float())
            loss_t = loss.item()
            running_loss += (loss_t - running_loss) / (batch_index + 1)

            # compute the accuracy
            acc_t = compute_accuracy(y_pred, batch_dict['y_target'])
            running_acc += (acc_t - running_acc) / (batch_index + 1)
            val_bar.set_postfix(loss=running_loss, acc=running_acc, 
                            epoch=epoch_index)
            val_bar.update()

        train_state_glove['val_loss'].append(running_loss)
        train_state_glove['val_acc'].append(running_acc)

        train_state_glove = update_train_state(args=args_glove, model=classifier_emb_tfidf,
                                         train_state=train_state_glove)

        scheduler.step(train_state_glove['val_loss'][-1])

        if train_state_glove['stop_early']:
            break

        train_bar.n = 0
        val_bar.n = 0
        epoch_bar.update()
except KeyboardInterrupt:
    print("Exiting loop")

training routine:   0%|          | 0/100 [00:00<?, ?it/s]

split=train:   0%|          | 0/162 [00:00<?, ?it/s]

split=val:   0%|          | 0/23 [00:00<?, ?it/s]

#### Exporting model

In [155]:
with open(f"{args_glove.save_dir}/ff_neuralNetwork_gloveEncoding_jobType.pth", "wb") as outp:
    pickle.dump(classifier_emb_tfidf, outp)


#### Evaluating model

In [156]:
# # compute the loss & accuracy on the test set using the best available model
# with open(f"{args_glove.save_dir}/ff_neuralNetwork_gloveEncoding_jobType.pth", "rb") as outp:
#     classifier_emb_tfidf= pickle.load( outp)
# classifier_emb_tfidf.load_state_dict(torch.load(train_state_glove['model_filename']))

# classifier_emb_tfidf = classifier_emb_tfidf.to(args_glove.device)

loss_func = nn.BCEWithLogitsLoss()

dataset.set_split('test')
batch_generator = generate_batches(dataset, 
                                   batch_size=args_glove.batch_size, 
                                   device=args_glove.device)
running_loss = 0.
running_acc = 0.
classifier_emb_tfidf.eval()

for batch_index, batch_dict in enumerate(batch_generator):
    # compute the output
    y_pred =  classifier_emb_tfidf(batch_dict['x_data'])
    
    # compute the loss
    loss = loss_func(y_pred, batch_dict['y_target'].float())
    loss_t = loss.item()
    running_loss += (loss_t - running_loss) / (batch_index + 1)

    # compute the accuracy
    acc_t = compute_accuracy(y_pred, batch_dict['y_target'])
    running_acc += (acc_t - running_acc) / (batch_index + 1)

train_state_glove['test_loss'] = running_loss
train_state_glove['test_acc'] = running_acc

In [157]:
print("Test loss: {};".format(train_state_glove['test_loss']))
print("Test Accuracy: {}".format(train_state_glove['test_acc']))

Test loss: 0.6177865584259448;
Test Accuracy: 76.80027173913045


## Word2vec encoding

#### Traingin vectorizer and creating vectorizer class

In [17]:
from time import time
from gensim.models import Word2Vec

cores = 16
word2vec_enc = Word2Vec(min_count=1,
                     window=2,
                     vector_size=100,
                     sample=6e-5, 
                     alpha=0.03, 
                     min_alpha=0.0007, 
                     negative=20,
                     workers=cores-1)

t = time()

word2vec_enc.build_vocab(df['job_description'], progress_per=10)

print('Time to build vocab: {} mins'.format(round((time() - t) / 60, 2)))

Time to build vocab: 0.03 mins


In [18]:
word2vec_enc.save('word2vec.bin')

In [21]:
w2v_M, w2v_key_to_index = get_matrix_of_vectors(word2vec_enc.wv, flat_list)

Shuffling words ...
Putting 10000 words into word2Ind and matrix M...
Done.


In [24]:
with open("final_description.pkl", "rb") as outp:
    final_description = pickle.load(outp)
    
w2v_job_type_vec = emb_Vectorizer.from_dataframe(final_description, target_cat = False) 
w2v_category_vec = emb_Vectorizer.from_dataframe(final_description, target_cat = True)
# swapping the document based word to ind for the pretained embedding based word to ind for description
w2v_job_type_vec.description_vocab = Vocabulary(token_to_idx=w2v_key_to_index, add_unk=True)
w2v_category_vec.description_vocab = Vocabulary(token_to_idx=w2v_key_to_index, add_unk=True)

In [25]:
with open("w2v_job_type_vec.pkl", "wb") as outp:
    pickle.dump(w2v_job_type_vec, outp)
   

with open("w2v_category_vec.pkl", "wb") as outp:
    pickle.dump(w2v_category_vec, outp)

#### Creating data set

In [26]:
with open("w2v_job_type_vec.pkl", "rb") as f:
    w2v_job_type_vec = pickle.load(f)
    

with open("w2v_category_vec.pkl", "rb") as f:
    w2v_category_vec = pickle.load(f)
    

In [29]:
dataset_w2v_tfidf_job_type = Dataset_embedding(final_description, w2v_job_type_vec)
dataset_w2v_full_desc_job_type = Dataset_embedding(final_description,w2v_job_type_vec, short = False)
dataset_w2v_full_desc_category = Dataset_embedding(final_description,w2v_category_vec, short = False, job_type = False)


In [30]:
with open("dataset_w2v_tfidf_job_type.pkl", "wb") as outp:
    pickle.dump(dataset_w2v_tfidf_job_type, outp)
   
    
with open("dataset_w2v_full_desc_job_type.pkl", "wb") as outp:
    pickle.dump(dataset_w2v_full_desc_job_type, outp)
    
with open("dataset_w2v_full_desc_category.pkl", "wb") as outp:
    pickle.dump(dataset_w2v_full_desc_category, outp)

In [40]:
args_w2v = Namespace(
    # Data and Path hyper parameters
    
    # Model hyper parameters 
    use_w2v=False, 
    hidden_dim=100, 
    input_size = 10, # derived from dataloader object
    vocab_siz = w2v_M.shape[0],
    embedding_dim = w2v_M.shape[1],
    target_dim = 2, # only need Full time and other.
    # Training hyper parameter
    seed=1337, 
    learning_rate=0.001, 
    batch_size=128,
    dropout_p=0.1, 
    num_epochs=100, 
    early_stopping_criteria=5, 
    # Runtime option
    cuda=True, 
    catch_keyboard_interrupt=True, 
    reload_from_files=False,
    expand_filepaths_to_save_dir=True,
    model_state_file="w2v_tfidf_model.pth",
    save_dir='./model_storage/document_classification/',
) 


    
# Check CUDA
if not torch.cuda.is_available():
    args_w2v.cuda = False
    
args_w2v.device = torch.device("cuda" if args_w2v.cuda else "cpu")
print("Using CUDA: {}".format(args_w2v.cuda))

# Set seed for reproducibility
set_seed_everywhere(args_w2v.seed, args_w2v.cuda)



Using CUDA: True


### Initialising

In [58]:
args_w2v.use_w2v = True


# dataset and vectorizer
with open("dataset_w2v_tfidf_job_type.pkl", "rb") as f:
    dataset = pickle.load(f)

vectorizer = dataset.get_vectorizer()

# Use w2v or randomly initialized embeddings
if args_w2v.use_w2v:
    words = vectorizer.description_vocab._token_to_idx.keys()
    w2v_embedding = make_embedding_matrix(words, embeddings=w2v_M, seed=args_w2v.seed, emb_dim=args_w2v.embedding_dim,word_to_idx=w2v_key_to_index)
    print("Using pre-trained embeddings")

# model
classifier_emb_tfidf_w2v = Classifier_emb(embedding_size=args_w2v.embedding_dim, 
                            num_embeddings=len(vectorizer.description_vocab),
                            hidden_dim=args_w2v.hidden_dim, 
                            input_size = args_w2v.input_size,
                            dropout_p=args_w2v.dropout_p,
                            pretrained_embeddings=w2v_embedding)

# loss and optimizer
loss_func = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(classifier_emb_tfidf_w2v.parameters(), lr=args_w2v.learning_rate)

Using pre-trained embeddings


In [59]:

classifier_emb_tfidf_w2v = classifier_emb_tfidf_w2v.to(args_w2v.device)
dataset.class_weights = dataset.class_weights.to(args_w2v.device)
    
loss_func = nn.BCEWithLogitsLoss()
optimizer = optim.Adam(classifier_emb_tfidf_w2v.parameters(), lr=args_w2v.learning_rate)
scheduler = optim.lr_scheduler.ReduceLROnPlateau(optimizer=optimizer,
                                           mode='min', factor=0.5,
                                           patience=1)

train_state_w2v = make_train_state(args_w2v)

epoch_bar = tqdm(desc='training routine', 
                          total=args_w2v.num_epochs,
                          position=0)

dataset.set_split('train')
train_bar = tqdm(desc='split=train',
                          total=dataset.get_num_batches(args_w2v.batch_size), 
                          position=1, 
                          leave=True)
dataset.set_split('val')
val_bar = tqdm(desc='split=val',
                        total=dataset.get_num_batches(args_w2v.batch_size), 
                        position=1, 
                        leave=True)

try:
    for epoch_index in range(args_w2v.num_epochs):
        train_state_w2v['epoch_index'] = epoch_index

        # Iterate over training dataset

        # setup: batch generator, set loss and acc to 0, set train mode on

        dataset.set_split('train')
        batch_generator = generate_batches(dataset, 
                                           batch_size=args_w2v.batch_size, 
                                           device=args_w2v.device)
        running_loss = 0.0
        running_acc = 0.0
        classifier_emb_tfidf_w2v.train()

        for batch_index, batch_dict in enumerate(batch_generator):
            # the training routine is these 5 steps:

            # --------------------------------------
            # step 1. zero the gradients
            optimizer.zero_grad()

            # step 2. compute the output
            y_pred = classifier_emb_tfidf_w2v(batch_dict['x_data'])

            # step 3. compute the loss
            loss = loss_func(y_pred, batch_dict['y_target'].float())
            loss_t = loss.item()
            running_loss += (loss_t - running_loss) / (batch_index + 1)

            # step 4. use loss to produce gradients
            loss.backward()

            # step 5. use optimizer to take gradient step
            optimizer.step()
            # -----------------------------------------
            # compute the accuracy
            acc_t = compute_accuracy(y_pred, batch_dict['y_target'])
            running_acc += (acc_t - running_acc) / (batch_index + 1)

            # update bar
            train_bar.set_postfix(loss=running_loss, acc=running_acc, 
                                  epoch=epoch_index)
            train_bar.update()

        train_state_w2v['train_loss'].append(running_loss)
        train_state_w2v['train_acc'].append(running_acc)

        # Iterate over val dataset

        # setup: batch generator, set loss and acc to 0; set eval mode on
        dataset.set_split('val')
        batch_generator = generate_batches(dataset, 
                                           batch_size=args_w2v.batch_size, 
                                           device=args_w2v.device)
        running_loss = 0.
        running_acc = 0.
        classifier_emb_tfidf_w2v.eval()

        for batch_index, batch_dict in enumerate(batch_generator):

            # compute the output
            y_pred =  classifier_emb_tfidf_w2v(batch_dict['x_data'])

            # step 3. compute the loss
            loss = loss_func(y_pred, batch_dict['y_target'].float())
            loss_t = loss.item()
            running_loss += (loss_t - running_loss) / (batch_index + 1)

            # compute the accuracy
            acc_t = compute_accuracy(y_pred, batch_dict['y_target'])
            running_acc += (acc_t - running_acc) / (batch_index + 1)
            val_bar.set_postfix(loss=running_loss, acc=running_acc, 
                            epoch=epoch_index)
            val_bar.update()

        train_state_w2v['val_loss'].append(running_loss)
        train_state_w2v['val_acc'].append(running_acc)

        train_state_w2v = update_train_state(args=args_w2v, model=classifier_emb_tfidf_w2v,
                                         train_state=train_state_w2v)

        scheduler.step(train_state_w2v['val_loss'][-1])

        if train_state_w2v['stop_early']:
            break

        train_bar.n = 0
        val_bar.n = 0
        epoch_bar.update()
except KeyboardInterrupt:
    print("Exiting loop")

training routine:   0%|          | 0/100 [00:00<?, ?it/s]

split=train:   0%|          | 0/162 [00:00<?, ?it/s]

split=val:   0%|          | 0/23 [00:00<?, ?it/s]

#### Exporting model

In [60]:
with open(f"{args_w2v.save_dir}/ff_neuralNetwork_w2vEncoding_jobType.pth", "wb") as outp:
    pickle.dump(classifier_emb_tfidf_w2v, outp)


#### Evaluating model

In [61]:
# compute the loss & accuracy on the test set using the best available model
with open(f"{args_w2v.save_dir}/ff_neuralNetwork_w2vEncoding_jobType.pth", "rb") as outp:
    classifier_emb_tfidf_w2v = pickle.load( outp)

classifier_emb_tfidf_w2v.load_state_dict(torch.load(train_state_w2v['model_filename']))

classifier_emb_tfidf_w2v = classifier_emb_tfidf_w2v.to(args_w2v.device)

loss_func = nn.BCEWithLogitsLoss()

dataset.set_split('test')
batch_generator = generate_batches(dataset, 
                                   batch_size=args_w2v.batch_size, 
                                   device=args_w2v.device)
running_loss = 0.
running_acc = 0.
classifier_emb_tfidf_w2v.eval()

for batch_index, batch_dict in enumerate(batch_generator):
    # compute the output
    y_pred =  classifier_emb_tfidf_w2v(batch_dict['x_data'])
    
    # compute the loss
    loss = loss_func(y_pred, batch_dict['y_target'].float())
    loss_t = loss.item()
    running_loss += (loss_t - running_loss) / (batch_index + 1)

    # compute the accuracy
    acc_t = compute_accuracy(y_pred, batch_dict['y_target'])
    running_acc += (acc_t - running_acc) / (batch_index + 1)

train_state_w2v['test_loss'] = running_loss
train_state_w2v['test_acc'] = running_acc

In [62]:
print("Test loss: {};".format(train_state_w2v['test_loss']))
print("Test Accuracy: {}".format(train_state_w2v['test_acc']))

Test loss: 0.5913682903932489;
Test Accuracy: 77.44565217391302


#### CNN 

In [139]:
print(word2vec_enc)

Word2Vec<vocab=18623, vector_size=100, alpha=0.03>


In [140]:
print(word2vec_enc['sentence'])

TypeError: 'Word2Vec' object is not subscriptable